In [1]:
# import library
import os
import pandas as pd
import numpy as np
np.random.seed(71)
import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles
import seaborn as sns
from tqdm.notebook import tqdm
import pathlib
import plotly
import plotly.express as px
import simdkalman
from scipy.interpolate import interp1d

from pathlib import Path
import pyproj
from pyproj import Proj, transform # 地理的な位置を示す情報を扱うときに、座標系・測地系変換を行ったり、2点間の距離・方位角を計算したりできる。
from pandarallel import pandarallel
pandarallel.initialize()

import optuna

INFO: Pandarallel will run on 8 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.


In [43]:
def calc_haversine(lat1, lon1, lat2, lon2):
    """Calculates the great circle distance between two points
    on the earth. Inputs are array-like and specified in decimal degrees.
    """
    RADIUS = 6_367_000
    lat1, lon1, lat2, lon2 = map(np.radians, [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = np.sin(dlat/2)**2 + \
        np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2)**2
    dist = 2 * RADIUS * np.arcsin(a**0.5)
    return dist

    
def percentile50(x):
    return np.percentile(x, 50)
def percentile95(x):
    return np.percentile(x, 95)

def get_train_score(df, gt):
    gt = gt.rename(columns={'latDeg':'latDeg_gt', 'lngDeg':'lngDeg_gt'})
    # df = df.merge(gt, on=['collectionName', 'phoneName', 'millisSinceGpsEpoch'], how='inner')
    df = df.merge(gt, on=['phone', 'millisSinceGpsEpoch'], how='inner')
    # calc_distance_error
    df['err'] = calc_haversine(df['latDeg_gt'], df['lngDeg_gt'], df['latDeg'], df['lngDeg'])
    # calc_evaluate_score
    # df['phone'] = df['collectionName'] + '_' + df['phoneName']
    res = df.groupby('phone')['err'].agg([percentile50, percentile95]) # phoneによってgroupbyし、gtと予測値の差(err)の50%,95%値を求める
    res['p50_p90_mean'] = (res['percentile50'] + res['percentile95']) / 2 
    score = res['p50_p90_mean'].mean()
    return score

def visualize_trafic(df, center={"lat":37.6458, "lon":-122.4056}, zoom=9):
    fig = px.scatter_mapbox(df,
                            # Here, plotly gets, (x,y) coordinates
                            lat="latDeg",
                            lon="lngDeg",
                            
                            #Here, plotly detects color of series
                            color="phone",
                            
                            labels="phone",
                            zoom=zoom,
                            center=center,
                            height=600,
                            width=800)
    fig.update_layout(mapbox_style='stamen-terrain')
    fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
    fig.update_layout(title_text="GPS trafic")
    fig.show()


In [18]:
# directory setting
INPUT = '../input/google-smartphone-decimeter-challenge'

base_train = pd.read_csv(INPUT + '/' + 'baseline_locations_train.csv')
train_df = pd.read_csv('../output/filtered_nb037.csv')
train_df['collectionName'] = train_df['phone'].map(lambda x: x.split('_')[0])
train_df['phoneName'] = train_df['phone'].map(lambda x: x.split('_')[1])

# base_test = pd.read_csv('../output/sub_nb037.csv')
test_df = pd.read_csv('../output/sub_nb037_5.csv')
# base_test = pd.read_csv('../output/fixed_base_test.csv')

sample_sub = pd.read_csv(INPUT + '/' + 'sample_submission.csv')

# ground_truth
p = pathlib.Path(INPUT)
gt_files = list(p.glob('train/*/*/ground_truth.csv'))
print('ground_truth.csv count : ', len(gt_files))

gts = []
for gt_file in tqdm(gt_files):
    gts.append(pd.read_csv(gt_file))
ground_truth = pd.concat(gts)
ground_truth['phone'] = ground_truth['collectionName'] + '_' + ground_truth['phoneName']

collection_uniq = train_df['collectionName'].unique()
SJC = [i for i in collection_uniq if 'SJC' in i]
MTV = [i for i in collection_uniq if 'MTV' in i]
SVL = [i for i in collection_uniq if 'SVL' in i]
SF = [i for i in collection_uniq if 'SF' in i]
RWC = [i for i in collection_uniq if 'RWC' in i]

test_collection_uniq = test_df['collectionName'].unique()
test_SJC = [i for i in test_collection_uniq if 'SJC' in i]
test_MTV = [i for i in test_collection_uniq if 'MTV' in i]
test_SVL = [i for i in test_collection_uniq if 'SVL' in i]
test_SF = [i for i in test_collection_uniq if 'SF' in i]
test_RWC = [i for i in test_collection_uniq if 'RWC' in i]


ground_truth.csv count :  73


  0%|          | 0/73 [00:00<?, ?it/s]

In [4]:
def add_distance_diff(df):
    df['latDeg_prev'] = df['latDeg'].shift(1)
    df['latDeg_next'] = df['latDeg'].shift(-1)
    df['lngDeg_prev'] = df['lngDeg'].shift(1)
    df['lngDeg_next'] = df['lngDeg'].shift(-1)
    df['phone_prev'] = df['phone'].shift(1)
    df['phone_next'] = df['phone'].shift(-1)
    
    df['dist_prev'] = calc_haversine(df['latDeg'], df['lngDeg'], df['latDeg_prev'], df['lngDeg_prev'])
    df['dist_next'] = calc_haversine(df['latDeg'], df['lngDeg'], df['latDeg_next'], df['lngDeg_next'])
    
    df.loc[df['phone']!=df['phone_prev'], ['latDeg_prev', 'lngDeg_prev', 'dist_prev']] = np.nan
    df.loc[df['phone']!=df['phone_next'], ['latDeg_next', 'lngDeg_next', 'dist_next']] = np.nan
    
    return df

In [5]:
T = 1.0
state_transition = np.array([[1, 0, T, 0, 0.5 * T ** 2, 0], [0, 1, 0, T, 0, 0.5 * T ** 2], [0, 0, 1, 0, T, 0],
                             [0, 0, 0, 1, 0, T], [0, 0, 0, 0, 1, 0], [0, 0, 0, 0, 0, 1]])
process_noise = np.diag([1e-5, 1e-5, 5e-6, 5e-6, 1e-6, 1e-6]) + np.ones((6, 6)) * 1e-9
observation_model = np.array([[1, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0]])
observation_noise = np.diag([5e-5, 5e-5]) + np.ones((2, 2)) * 1e-9

kf = simdkalman.KalmanFilter(
        state_transition = state_transition,
        process_noise = process_noise,
        observation_model = observation_model,
        observation_noise = observation_noise)

def apply_kf_smoothing(df_, kf_=kf):
    df = df_.copy()
    unique_paths = df[['collectionName', 'phoneName']].drop_duplicates().to_numpy()
    for collection, phone in unique_paths:
        cond = np.logical_and(df['collectionName'] == collection, df['phoneName'] == phone)
        data = df[cond][['latDeg', 'lngDeg']].to_numpy()
        data = data.reshape(1, len(data), 2)
        smoothed = kf_.smooth(data)
        df.loc[cond, 'latDeg'] = smoothed.states.mean[0, :, 0]
        df.loc[cond, 'lngDeg'] = smoothed.states.mean[0, :, 1]
    return df

In [49]:
train = base_train.copy()
# reject outlier
train_ro = add_distance_diff(train)
th = 45
train_ro.loc[((train_ro['dist_prev'] > th) | (train_ro['dist_next'] > th)), ['latDeg', 'lngDeg']] = np.nan

# kalman filter
cols = ['collectionName', 'phoneName', 'millisSinceGpsEpoch', 'latDeg', 'lngDeg']
train_ro_kf = apply_kf_smoothing(train_ro[cols])

# phone
train_ro_kf['phone'] = train_ro_kf['collectionName'] + '_' + train_ro_kf['phoneName']

# score
print(get_train_score(base_train, ground_truth))
print(get_train_score(train_ro, ground_truth))
print(get_train_score(train_ro_kf, ground_truth))

5.287970649047861
3.901411670665515
4.504564902132495


In [ ]:
5.287970649047861
3.772967796404595
4.510036130040074

In [ ]:
5.287970649047861
3.930670201454808
4.498849117070059

In [ ]:
5.287970649047861
4.286618533626948
5.221773998775429

In [44]:
print(get_train_score(base_train, ground_truth))

5.287970649047861


In [45]:
visualize_trafic(train_ro_kf)